In [1]:
import pandas as pd
import numpy as np

In [14]:
# load
tweets = pd.read_csv('data/ukraine/UkraineCombinedTweetsDeduped_FEB27.csv')
tweets = tweets[tweets.language == 'en']
tweets.drop('Unnamed: 0',axis=1,inplace=True)
tweets.shape

(227513, 17)

In [17]:
len(tweets.userid.unique())

158184

In [3]:
# drop unique user ids
non_unique = tweets[tweets.duplicated(subset='userid',keep=False)]
non_unique.reset_index(inplace=True)
del tweets

In [4]:
# only interested in userid and creation time right now
users_times = non_unique[['userid','tweetcreatedts']]
users_times['tweetcreatedts'] = pd.to_datetime(users_times.tweetcreatedts).values.astype(np.int64)
del non_unique

/tmp/ipykernel_41453/2621844804.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  users_times['tweetcreatedts'] = pd.to_datetime(users_times.tweetcreatedts).values.astype(np.int64)


In [5]:
# dictionary with list of all post times attached to userid
times_dict = users_times.groupby('userid')['tweetcreatedts'].apply(list).to_dict()
del users_times

In [6]:
# transpose to cols by userid, cols filled with post times and empy spots filled with NaNs
timeseries = pd.DataFrame.from_dict(times_dict,orient='index').T
del times_dict

In [7]:
# find the bots! the easy ones anyway
bots = timeseries.corr(method='pearson',min_periods=4) # pearson == only positive corr
del timeseries

In [8]:
# remove self correlation
np.fill_diagonal(bots.values, 0)

In [9]:
sum0 = bots.sum()

In [13]:
sum0[sum0>0].sort_values(ascending=False)

2758100418             6406.690738
169433608              6406.604723
1420510424697610252    6406.145441
39565575               6405.417779
1252854227547729921    6404.559219
                          ...     
259584974              4237.422438
2850509662             4212.169727
82210282               4210.726707
1310836644946145286    4206.247469
85844581               4162.165699
Length: 7100, dtype: float64

In [ ]:
# 